# Proyecto 7 Aplicación Web "CarTrack"
El objetivo es subir una aplicación web que permita comparar algunas características en la venta de autos.

## 1. Preparación de los datos

In [1]:
# Librerías
import numpy as np
import pandas as pd
import plotly_express as px


# Carga de dataset .csv
car_data = pd.read_csv('/Users/irmalupita/proyecto_7/repo_vehicles/vehicles_us.csv') 
car_data.head(10)

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   
5  14990      2014.0    chrysler 300  excellent        6.0  gas   57954.0   
6  12990      2015.0    toyota camry  excellent        4.0  gas   79212.0   
7  15990      2013.0     honda pilot  excellent        6.0  gas  109473.0   
8  11500      2012.0     kia sorento  excellent        4.0  gas  104174.0   
9   9200      2008.0     honda pilot  excellent        NaN  gas  147191.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28  
5    automatic   sedan       black     1.0  2018-06-20           15  
6    automatic   sedan       white     NaN  2018-12-27           73  
7    automatic     SUV       black     1.0  2019-01-07           68  
8    automatic     SUV         NaN     1.0  2018-07-16           19  
9    automatic     SUV        blue     1.0  2019-02-15           17

In [2]:
# Revisión general de los datos
car_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


## 2. Procesamiento de datos
### 2.1. Valores NAN
#### 2.1.1 Valores NAN en columna 'model_year'

- Rellenamos los valores ausentes en model_year con el promedio del año de modelo según el tipo de carrocería. 

- Cambiamos el tipo de dato de float a int.

In [3]:
# Calcular la media del 'model_year' por cada 'type' de carrocería
mean_model_year_by_type = car_data.groupby('type')['model_year'].mean()

# Crear una función que reemplaza NaN con la media por 'type'
def fillna_by_type(row):
    if pd.isna(row['model_year']):
        return mean_model_year_by_type[row['type']]
    else:
        return row['model_year']

# Aplicar la función a la columna 'model_year'
car_data['model_year'] = car_data.apply(fillna_by_type, axis=1)

# Redondear los valores de 'model_year' antes de convertir a entero
car_data['model_year'] = car_data['model_year'].round()

# Convertir 'model_year' de float a int
car_data['model_year'] = car_data['model_year'].astype('Int64')


#### 2.1.2 Valores NAN en columna 'is_4wd'

Rellenamos los valores nan con 0 y cambiamos el tipo de datos de float64 a int

In [4]:
# Reemplazar NaN por 0 usando
car_data['is_4wd'] = car_data['is_4wd'].fillna(0).astype(int)

# Ver el tipo de datos para verificar
car_data.head()


price  model_year           model  condition  cylinders fuel  odometer  \
0   9400        2011          bmw x5       good        6.0  gas  145000.0   
1  25500        2009      ford f-150       good        6.0  gas   88705.0   
2   5500        2013  hyundai sonata   like new        4.0  gas  110000.0   
3   1500        2003      ford f-150       fair        8.0  gas       NaN   
4  14900        2017    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN       1  2018-06-23           19  
1    automatic  pickup       white       1  2018-10-19           50  
2    automatic   sedan         red       0  2019-02-07           79  
3    automatic  pickup         NaN       0  2019-03-22            9  
4    automatic   sedan       black       0  2019-04-02           28

#### 2.1.3 Valores NAN en la columna 'cylinders'
Reemplazamos los valores NaN en la columna cylinders usando la moda por modelo de coche.

In [5]:
# Reemplazar NaN en 'cylinders' con la moda por cada 'model'
car_data['cylinders'] = car_data.groupby('model')['cylinders'].transform(lambda x: x.fillna(x.mode()[0]))

# Verificar si aún hay valores NaN 
print(car_data['cylinders'].isna().sum())


0


#### 2.1.4 Valores NAN en la columna 'odometer'

**Observaciones**

Se intentó reemplazar los valores NAN en la columna 'odometer' con el promedio de millas por categoría en 'condition'. Y cambiar el tipo de dato a int. Sin embargo, se observó que los valores de kilometraje no siguen un patrón consistente según la condición del vehículo (por ejemplo, los autos "nuevos" presentan valores de kilometraje elevados, lo que no es lógico). Debido a la falta de un rango definido de millaje para cada categoría de condición (nuevo, seminuevo, etc.), se pospone el tratamiento de los valores NAN en esta columna hasta realizar una limpieza más detallada de los datos.


In [6]:
# Agrupar los datos por 'condition' y calcular el promedio de 'odometer' redondeado para cada grupo
average_odometer_by_condition = car_data.groupby('condition')['odometer'].mean().round()

# Mostrar los resultados
print(average_odometer_by_condition)


condition
excellent    106688.0
fair         183062.0
good         129920.0
like new      79427.0
new           43476.0
salvage      140920.0
Name: odometer, dtype: float64


In [7]:
# Agrupar por 'condition' y obtener el valor mínimo y máximo de 'odometer' para cada grupo
odometer_min_max = car_data.groupby('condition')['odometer'].agg(['min', 'max'])

print(odometer_min_max)


           min       max
condition               
excellent  0.0  980000.0
fair       0.0  500000.0
good       0.0  990000.0
like new   0.0  990000.0
new        5.0  315000.0
salvage    0.0  482000.0


### 2.2 Valores duplicados

**Observación:** 

No se hallaron valores duplicados.

In [8]:
print(car_data.duplicated().sum())

0


### 2.3 Creación de nueva columna 'manufacturer'

In [9]:
# Crear la nueva columna 'manufacturer' extrayendo la primera palabra de 'model'
car_data['manufacturer'] = car_data['model'].str.split().str[0]

# Ver los primeros registros para verificar
print(car_data[['model', 'manufacturer']].head(20))


                       model manufacturer
0                     bmw x5          bmw
1                 ford f-150         ford
2             hyundai sonata      hyundai
3                 ford f-150         ford
4               chrysler 200     chrysler
5               chrysler 300     chrysler
6               toyota camry       toyota
7                honda pilot        honda
8                kia sorento          kia
9                honda pilot        honda
10  chevrolet silverado 1500    chevrolet
11              honda accord        honda
12                  ram 1500          ram
13            hyundai sonata      hyundai
14                 gmc yukon          gmc
15                  ram 1500          ram
16                  ram 1500          ram
17             jeep cherokee         jeep
18        chevrolet traverse    chevrolet
19           hyundai elantra      hyundai


In [10]:
# Ver los valores únicos y su conteo en la columna 'manufacturer'
manufacturer_counts = car_data['manufacturer'].value_counts()

# Mostrar el resultado
print(manufacturer_counts)


manufacturer
ford             12672
chevrolet        10611
toyota            5445
honda             3485
ram               3316
jeep              3281
nissan            3208
gmc               2378
subaru            1272
dodge             1255
hyundai           1173
volkswagen         869
chrysler           838
kia                585
cadillac           322
buick              271
bmw                267
acura              236
mercedes-benz       41
Name: count, dtype: int64


## 3. Análisis Exploratorio

### 3.1 Relación entre precio y otras variables

In [11]:
# Crear el gráfico de dispersión interactivo
fig = px.scatter(car_data, x='model_year', y='price', 
                 title="Relación entre Año del Modelo y Precio",
                 labels={"model_year": "Año del Modelo", "price": "Precio"})
# Limitar el rango del eje Y hasta 200,000
fig.update_layout(yaxis=dict(range=[0, 200000]))
fig.show()


**Comentarios**
Se esperaba una tendencia donde los autos más nuevos tienen precios más altos, mientras que los modelos más antiguos presentan una gran dispersión de precios. Sin embargo se observan algunos puntos aislados en el gráfico.

- Los autos más viejos tienen precios bajos en su mayoría, pero las excepciones podrían ser autos clásicos o de colección que implica restauraciones con costos elevados.

- A partir del año 2000, los precios varían mucho dentro de un mismo año de modelo. Esto puede deberse a diferencias en la marca, el estado del vehículo, la demanda o el kilometraje o millaje.



#### Precio según la condición del auto

In [12]:
# Crear gráfico de dispersión para 'Precio' vs 'Condición'
fig = px.box(car_data, x='condition', y='price', 
             title='Precio según la Condición del Vehículo', 
             labels={'condition': 'Condición', 'price': 'Precio'})

fig.update_layout(yaxis=dict(range=[0, 200000]))

fig.show()


**Comentarios**

Observando el precio según la condición del vehículo, se nota que hay dispersión en los precios de los vehículos en "good" y "like new", lo que indica que hay factores adicionales que influyen en el precio, más allá de solo la condición.

### 3.2 Relación entre fabricante y otras variables

**Comentarios**

Se analiza la estabilidad de precios según la marca o fabricante y el tipo de combustible.

In [13]:
# Filtrar autos con modelo 2022 en adelante y precio menor o igual a 200,000
df_recent = car_data[(car_data['model_year'] >= 2002) & (car_data['price'] <= 200000)]  

# Crear el boxplot con color por tipo de combustible
fig = px.box(df_recent, x='manufacturer', y='price', color='fuel',  
             title='Distribución de Precios por Marca y Tipo de Combustible (Modelos 2002 en adelante, ≤200K)',  
             labels={'manufacturer': 'Marca', 'price': 'Precio', 'fuel': 'Tipo de Combustible'})  

# Mostrar la gráfica
fig.show()

**Observaciones generales:**
Marcas con mayor dispersión de precios: BMW, Ford y Chevrolet tienen muchos outliers y una amplia variabilidad de precios.
Marcas con precios más bajos y estables: Acura, Buick y Volkswagen tienen cajas más pequeñas, lo que indica menos variabilidad en los precios.
Tipos de combustible:
La mayoría de los autos usan gasolina (gas), lo que se nota porque dominan la cantidad de puntos.
Diesel, híbridos y eléctricos parecen menos comunes en la muestra.
